In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# split_data


In [ ]:
!mkdir ckpts
!mkdir reports
!mkdir results

In [ ]:
!pip install GPUtil pytorch_pretrained_bert transformers
!pip install barbar
# !pip uninstall emoji
!pip install emoji==1.7
!pip install emojis
!pip install --upgrade urllib3
!pip install brokenaxes

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.8/123.8 kB 1.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.3/139.3 kB 10.3 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cac

In [ ]:
from brokenaxes import brokenaxes
from numpy.random import RandomState
import operator
from scipy.interpolate import make_interp_spline
from sklearn.metrics import classification_report, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns
import json

from sklearn.metrics import accuracy_score, f1_score, classification_report
import torch
from torch.utils.data import Dataset
from transformers import AutoTokenizer, AutoModel
import torch.nn as nn
import torch.nn.functional as F
import argparse
import numpy as np
import pandas as pd
import random
from transformers import AdamW, get_linear_schedule_with_warmup
from barbar import Bar
from sklearn.model_selection import train_test_split
from torch.utils.data import Dataset, DataLoader
import os
import re
from emoji import UNICODE_EMOJI
import sys
import emojis
import numpy
import shutil

from statistics import mean
import math
from torch.autograd import Variable

In [ ]:
folder_path = 'Tuning'

In [ ]:
class FocalLoss_Ori(nn.Module):
    """
    This is a implementation of Focal Loss with smooth label cross entropy supported which is proposed in
    'Focal Loss for Dense Object Detection. (https://arxiv.org/abs/1708.02002)'
    Focal_Loss= -1*alpha*((1-pt)**gamma)*log(pt)
    Args:
        num_class: number of classes
        alpha: class balance factor
        gamma:
        ignore_index:
        reduction:
    """

    def __init__(self, num_class, alpha=None, gamma=2, ignore_index=None, reduction='mean'):
        super(FocalLoss_Ori, self).__init__()
        self.num_class = num_class
        self.gamma = gamma
        self.reduction = reduction
        self.smooth = 1e-4
        self.ignore_index = ignore_index
        self.alpha = alpha
        if alpha is None:
            self.alpha = torch.ones(num_class, )
        elif isinstance(alpha, (int, float)):
            self.alpha = torch.as_tensor([alpha] * num_class)
        elif isinstance(alpha, (list, np.ndarray)):
            self.alpha = torch.as_tensor(alpha)
        if self.alpha.shape[0] != num_class:
            raise RuntimeError('the length not equal to number of class')

    def forward(self, logit, target):
        # assert isinstance(self.alpha,torch.Tensor)\
        N, C = logit.shape[:2]
        alpha = self.alpha.to(logit.device)
        prob = F.softmax(logit, dim=1)
        if prob.dim() > 2:
            # N,C,d1,d2 -> N,C,m (m=d1*d2*...)
            prob = prob.view(N, C, -1)
            prob = prob.transpose(1, 2).contiguous()  # [N,C,d1*d2..] -> [N,d1*d2..,C]
            prob = prob.view(-1, prob.size(-1))  # [N,d1*d2..,C]-> [N*d1*d2..,C]
        ori_shp = target.shape
        target = target.view(-1, 1)  # [N,d1,d2,...]->[N*d1*d2*...,1]
        valid_mask = None
        if self.ignore_index is not None:
            valid_mask = target != self.ignore_index
            target = target * valid_mask

        # ----------memory saving way--------
        prob = prob.gather(1, target).view(-1) + self.smooth  # avoid nan
        logpt = torch.log(prob)
        # alpha_class = alpha.gather(0, target.view(-1))
        alpha_class = alpha[target.squeeze().long()]
        class_weight = -alpha_class * torch.pow(torch.sub(1.0, prob), self.gamma)
        loss = class_weight * logpt
        if valid_mask is not None:
            loss = loss * valid_mask.squeeze()

        if self.reduction == 'mean':
            loss = loss.mean()
            if valid_mask is not None:
                loss = loss.sum() / valid_mask.sum()

        elif self.reduction == 'none':
            loss = loss.view(ori_shp)
        return loss



In [ ]:
def split_data(data_name):
      if(data_name == 'ArSarcasm'):
        df  = pd.read_csv('/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm/ArSarcasm_train.csv')
        folder = '/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm/split/'
        df['sarcasm'] = df['sarcasm'].map({True: 1, False: 0})
        df.rename(columns = {'sarcasm':'sarcastic'}, inplace = True)

      elif(data_name == 'ArSarcasm_v2'):
        df  = pd.read_csv('/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm_v2/training_data.csv')
        folder = '/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm_v2/split/'
        df['sarcasm'] = df['sarcasm'].map({True: 1, False: 0})
        df.rename(columns = {'sarcasm':'sarcastic'}, inplace = True)

      rng = RandomState()
      data = df.sample(frac=1).reset_index(drop=True)
      train, test = train_test_split(data, test_size=0.2, stratify=data["sarcastic"].values, random_state=42, shuffle=True)#

      train.to_csv('train.csv')
      test.to_csv('val.csv')

      shutil.copy('train.csv', f"{folder}train.csv")
      shutil.copy('val.csv', f"{folder}val.csv")


In [ ]:
class TrainDataset(Dataset):
    def __init__(self, df, pretraine_path='xlm-roberta-base', max_length=128):
        self.df = df
        self.max_length = max_length

        self.tokenizer = AutoTokenizer.from_pretrained(pretraine_path)

    def __getitem__(self, index):
        text = self.df.iloc[index]['tweet']
        sarc_label = self.df.iloc[index]["sarcastic"]
        sent_label = self.df.iloc[index]["sentiment"]

        encoded_input = self.tokenizer(
                text,
                max_length = self.max_length,
                padding='max_length',
                truncation=True,
                return_tensors="pt",
            )

        input_ids = encoded_input["input_ids"]
        attention_mask = encoded_input["attention_mask"] if "attention_mask" in encoded_input else None

        data_input = {
            "input_ids":input_ids.flatten(),
            "attention_mask": attention_mask.flatten()
        }

        sarc_label_input ={
            "sarcasm": torch.tensor(sarc_label, dtype=torch.float),
        }
        sent_label_input ={
            "sentiment": torch.tensor(sent_label, dtype=torch.float),
        }

        return data_input, sarc_label_input, sent_label_input

    def __len__(self):
        return self.df.shape[0]

In [ ]:
def label_rule(mis_preds, cat_preds):
    for i in range(len(mis_preds)):
        if mis_preds[i] == 0:
            cat_preds[i] = 0
    return cat_preds


def accuracy(preds, y):
    all_output = preds.float().cpu()
    all_label = y.float().cpu()
    _, predict = torch.max(all_output, 1)
    acc = accuracy_score(all_label.numpy(), torch.squeeze(predict).float().numpy())
    return acc

def calc_accuracy(preds,y):
    predict = torch.argmax(preds, dim=1)
    accuracy = torch.sum(predict == y.squeeze()).float().item()
    return accuracy / float(preds.size()[0])

def calc_f1_sarcasm(preds,y):

    predict = torch.argmax(preds, dim=1)
    f1_sarcastic = f1_score(y, predict, average='binary', pos_label=1)
    return f1_sarcastic

def calc_f1_score(preds,y):
    predict = torch.argmax(preds, dim=1)
    f1_score_macro = f1_score(y, predict, average='macro')
    return f1_score_macro

def binary_accuracy2(preds, y):
    # round predictions to the closest integer
    rounded_preds = torch.round(preds).squeeze()

    correct = (rounded_preds == y).float()
    acc = correct.sum() / (y.size(0))
    return acc

def binary_accuracy(preds, y):
    # round predictions to the closest integer
    rounded_preds = torch.round(preds).squeeze()

    correct = (rounded_preds == y).float()
    acc = correct.sum() / (y.size(0) * y.size(1))
    return acc

In [ ]:
folder_dic = {
    "ArSarcasm": '/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm',
    "ArSarcasm_v2": '/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm_v2'
}

In [ ]:
dic= {
      "egypt": 'المصرية',
			"nile": 'المصرية',
			"msa": "اللغة العربية الفصحى",
			"magreb": "المغربية",
			"gulf": "الخليجية",
			"levant": "الشامية"
}

In [ ]:
def is_emoji(s):
    return s in UNICODE_EMOJI

# add space near your emoji
def add_space(text):
    return ''.join(' ' + char if is_emoji(char) else char for char in text).strip()

def preprocess(text):
    sent = add_space(text)
    sent = re.sub(r'(?:@[\w_]+)', "user", sent)
    sent = re.sub(r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+', "url", sent)
    sent = sent.replace('_', ' ')
    sent = sent.replace('#', ' ')
    return sent

def prepare_text(df, col):
    if col == 'tweet':
        df['dialect'] = df['dialect'].map(dic)
    for i in range(df.shape[0]):
        df.loc[i, col] = df.loc[i, 'dialect'] + ' [SEP] ' + df.loc[i, col]

    return df


In [ ]:
def init_weights(m):
    classname = m.__class__.__name__
    if classname.find('Conv2d') != -1 or classname.find('ConvTranspose2d') != -1:
        nn.init.kaiming_uniform_(m.weight)
        nn.init.zeros_(m.bias)
    elif classname.find('BatchNorm') != -1:
        nn.init.normal_(m.weight, 1.0, 0.02)
        nn.init.zeros_(m.bias)
    elif classname.find('Linear') != -1:
        nn.init.xavier_normal_(m.weight)
        if m.bias is not None:
            nn.init.zeros_(m.bias)

class TransformerLayer(nn.Module):
    def __init__(self,both=True,
                pretrained_path='aubmindlab/bert-base-arabert'):
        super(TransformerLayer, self).__init__()

        self.both = both
        self.transformer = AutoModel.from_pretrained(pretrained_path, output_hidden_states=True)

    def forward(self, input_ids=None, attention_mask=None):
        outputs = self.transformer(
            input_ids=input_ids,
            attention_mask=attention_mask
        )
        # (output_last_layer, pooled_cls, (output_layers))
        # output[0] (8, seqlen=64, 768) cls [8, 768] ( 12 (8, seqlen=64, 768))

        return outputs

    def output_num(self):
        return self.transformer.config.hidden_size


In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
def evaluate(base_model, mt_classifier, iterator, sar_criterion, sent_criterion):
    # initialize every epoch
    acc_sarcasm= 0
    acc_sentiment= 0
    f1_sarcasm =0
    f1_score_macro = 0
    loss= 0

    #all_sarcasm_outputs = []
    all_sarcasm_outputs = np.array([])
    all_sarcasm_labels = np.array([])
    all_sentiment_outputs = np.array([])
    all_sentiment_labels = np.array([])

    # set the model in eval phase
    base_model.eval()
    mt_classifier.eval()
    with torch.no_grad():
        for data_input, sarc_label_input, sent_label_input  in Bar(iterator):

            for k, v in data_input.items():
                data_input[k] = v.to(device)

            for k, v in sarc_label_input.items():
                sarc_label_input[k] = v.long().to(device)

            for k, v in sent_label_input.items():
                sent_label_input[k] = v.long().to(device)



            sarcasm_target = sarc_label_input['sarcasm']
            sentiment_target = sent_label_input['sentiment']

            # forward pass

            output = base_model(**data_input)
            sarcasm_logits , sentiment_logits = mt_classifier(output)
            # logits = sarcasm_logits[:,:2]

            sarcasm_probs = torch.softmax(sarcasm_logits, dim=1)
            sentiment_probs = torch.softmax(sentiment_logits, dim=1)

            # compute the loss
            loss_sarcasm = sar_criterion(sarcasm_logits, sarcasm_target)
            loss_sentiment = sent_criterion(sentiment_logits, sentiment_target)

            loss_ = loss_sarcasm + loss_sentiment

            # compute the running accuracy and losses
            acc_sarcasm += calc_accuracy(sarcasm_probs, sarcasm_target)
            _, predicted_sarcasm = torch.max(sarcasm_probs, 1)

            acc_sentiment += calc_accuracy(sentiment_probs, sentiment_target)
            _, predicted_sentiment = torch.max(sentiment_probs, 1)

            all_sarcasm_outputs = np.append(all_sarcasm_outputs, predicted_sarcasm.squeeze().cpu().numpy())
            all_sarcasm_labels = np.append(all_sarcasm_labels, sarcasm_target.squeeze().cpu().numpy())

            all_sentiment_outputs = np.append(all_sentiment_outputs, predicted_sentiment.squeeze().cpu().numpy())
            all_sentiment_labels = np.append(all_sentiment_labels, sentiment_target.squeeze().cpu().numpy())

    all_sarcasm_outputs = all_sarcasm_outputs.reshape(-1)
    all_sarcasm_labels = all_sarcasm_labels.reshape(-1)

    fscore_macro_sarc = f1_score(y_true=all_sarcasm_labels, y_pred=all_sarcasm_outputs, average='macro')
    fscore_sarcasm = f1_score(all_sarcasm_labels, all_sarcasm_outputs, average='binary', pos_label=1)

    all_sentiment_outputs = all_sentiment_outputs.reshape(-1)
    all_sentiment_labels = all_sentiment_labels.reshape(-1)

    fscore_macro_sent = f1_score(y_true=all_sentiment_labels, y_pred=all_sentiment_outputs, average='macro')

    report_sarcasm = classification_report(y_true=all_sarcasm_labels, y_pred=all_sarcasm_outputs,digits=4)


    # accuracies = { 'accuracy': acc_sarcasm / len(iterator), 'f1_sarcastic': fscore_sarcasm, "f1_score": fscore_macro, 'report_sarcasm': report_sarcasm}
    accuracies = { 'acc_sarc': acc_sarcasm / len(iterator), 'f1_sarcastic': fscore_sarcasm, "f1_score_sarc": fscore_macro_sarc,
                   'acc_sent': acc_sentiment / len(iterator), "f1_score_sent": fscore_macro_sent}
    losses = { 'loss': loss_ / len(iterator)}

    return accuracies, losses


In [ ]:
def predict(base_model, mt_classifier, iterator):
    # initialize every epoch
    acc_sarcasm= 0
    acc_sentiment= 0
    loss= 0

    f1_sarcasm =0
    f1_score_macro = 0

    #all_sarcasm_outputs = []
    all_sarcasm_outputs = np.array([])
    all_sarcasm_labels = np.array([])
    all_sentiment_outputs = np.array([])
    all_sentiment_labels = np.array([])

    # set the model in eval phase
    base_model.eval()
    mt_classifier.eval()
    with torch.no_grad():
      for data_input, sarc_label_input, sent_label_input  in Bar(iterator):

            for k, v in data_input.items():
                data_input[k] = v.to(device)

            for k, v in sarc_label_input.items():
                sarc_label_input[k] = v.long().to(device)

            for k, v in sent_label_input.items():
                sent_label_input[k] = v.long().to(device)

            sarcasm_target = sarc_label_input['sarcasm']
            sentiment_target = sent_label_input['sentiment']

            # forward pass

            output = base_model(**data_input)
            sarcasm_logits , sentiment_logits = mt_classifier(output)
            # logits = sarcasm_logits[:,:2]
            sarcasm_probs = torch.softmax(sarcasm_logits, dim=1)
            sentiment_probs = torch.softmax(sentiment_logits, dim=1)

            # compute the loss
            acc_sarcasm += calc_accuracy(sarcasm_probs, sarcasm_target)
            _, predicted_sarcasm = torch.max(sarcasm_probs, 1)

            acc_sentiment += calc_accuracy(sentiment_probs, sentiment_target)
            _, predicted_sentiment = torch.max(sentiment_probs, 1)

            #all_sarcasm_outputs.extend(predicted_sarcasm.squeeze().int().cpu().numpy().tolist())
            all_sarcasm_outputs = np.append(all_sarcasm_outputs, predicted_sarcasm.squeeze().cpu().numpy())
            all_sarcasm_labels = np.append(all_sarcasm_labels, sarcasm_target.squeeze().cpu().numpy())

            all_sentiment_outputs = np.append(all_sentiment_outputs, predicted_sentiment.squeeze().cpu().numpy())
            all_sentiment_labels = np.append(all_sentiment_labels, sentiment_target.squeeze().cpu().numpy())

    all_sarcasm_outputs = all_sarcasm_outputs.reshape(-1)
    all_sarcasm_labels = all_sarcasm_labels.reshape(-1)

    fscore_macro_sarc = f1_score(y_true=all_sarcasm_labels, y_pred=all_sarcasm_outputs, average='macro')
    fscore_sarcasm = f1_score(all_sarcasm_labels, all_sarcasm_outputs, average='binary', pos_label=1)

    all_sentiment_outputs = all_sentiment_outputs.reshape(-1)
    all_sentiment_labels = all_sentiment_labels.reshape(-1)

    fscore_macro_sent = f1_score(y_true=all_sentiment_labels, y_pred=all_sentiment_outputs, average='macro')

    report_sarcasm = classification_report(y_true=all_sarcasm_labels, y_pred=all_sarcasm_outputs,digits=4)

    accuracies = { 'acc_sarc': acc_sarcasm / len(iterator), 'f1_sarcastic': fscore_sarcasm, "f1_score_sarc": fscore_macro_sarc,
                   'acc_sent': acc_sentiment / len(iterator), "f1_score_sent": fscore_macro_sent}

    # accuracies = { 'accuracy': acc_sarcasm / len(iterator), 'f1_sarcastic': fscore_sarcasm, "f1_score": fscore_macro, 'report_sarcasm': report_sarcasm}
    return accuracies, all_sarcasm_outputs, all_sarcasm_labels,  all_sentiment_outputs, all_sentiment_labels


In [ ]:
results_h = f'drive/MyDrive/iSarcasm/{folder_path}/bert/results/results_h.jsonl'
results_h_2 = f'drive/MyDrive/iSarcasm/{folder_path}/bert/results/results_h_2.jsonl'
results_t = f'drive/MyDrive/iSarcasm/{folder_path}/bert/results/results_t.jsonl'
results_t_2 = f'drive/MyDrive/iSarcasm/{folder_path}/bert/results/results_t_2.jsonl'

In [ ]:
dic_labels ={
    "NEG": 0,
    "NEU": 1,
    "POS": 2
}

In [ ]:
def loadTrainValData2(data_name="ArSarcasm_v2",size=0.2, batchsize=16, num_worker=0, pretraine_path="marbert", seed=42, max_length=128):
    path = "/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm_v2/split/train.csv"
    data = pd.read_csv(path, encoding='utf-8')
    data = data[~data.tweet.isna()]
    data['tweet'] = data['tweet'].apply(lambda x: preprocess(x))
    data = prepare_text(data, col='tweet')
    for i in range (len(data['sentiment'])):
        data['sentiment'][i] = dic_labels[data['sentiment'][i]]

    data = data[["tweet", "sarcastic", "sentiment"]]
    data = data.sample(frac=1).reset_index(drop=True)
    # data.head(10)
    df_train = data
    df_train = df_train.sample(frac=1).reset_index(drop=True)
    path = "/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm_v2/split/val.csv"
    data = pd.read_csv(path, encoding='utf-8')
    data = data[~data.tweet.isna()]
    data['tweet'] = data['tweet'].apply(lambda x: preprocess(x))
    data = prepare_text(data, col='tweet')
    for i in range (len(data['sentiment'])):
        data['sentiment'][i] = dic_labels[data['sentiment'][i]]
    # data.head(10)
    df_test = data
    DF_train = TrainDataset(df_train, pretraine_path, max_length)
    DF_test = TrainDataset(df_test, pretraine_path, max_length)

    DF_train_loader = DataLoader(dataset=DF_train, batch_size=batchsize, shuffle=True,
                                 num_workers=num_worker)
    DF_test_loader = DataLoader(dataset=DF_test, batch_size=batchsize, shuffle=False,
                                num_workers=num_worker)
    return DF_train_loader, DF_test_loader

In [ ]:
def loadTestData(data_name, batchsize=16, num_worker=2, pretraine_path="xlm-roberta-base", max_length=128):

    path = "/content/drive/MyDrive/iSarcasm/Datasets3/ArSarcasm_v2/split/test.csv"
    data = pd.read_csv(path, encoding='utf-8')
    data['tweet'] = data['tweet'].apply(lambda x:preprocess(x))
    data = prepare_text(data, col='tweet')
    for i in range (len(data['sentiment'])):
        data['sentiment'][i] = dic_labels[data['sentiment'][i]]
    data = data[["tweet", "sarcastic", "sentiment"]]
    DF_test = TrainDataset(data, pretraine_path, max_length)
    DF_test_loader = DataLoader(dataset=DF_test, batch_size=batchsize, shuffle=False,
                                num_workers=num_worker)

    return DF_test_loader

In [ ]:
class ATTClassifier(nn.Module):
    def __init__(self, in_feature, class_num_sarc=1, class_num_sent=3, dropout_prob=0.2):
        super(ATTClassifier, self).__init__()
        self.fc11 = nn.Linear(in_feature, 512)
        self.fc21 = nn.Linear(in_feature, 512)

        self.fc12  = nn.Linear(512, class_num_sarc)
        self.fc22= nn.Linear(512, class_num_sent)

        self.r1= nn.ReLU()
        self.r2= nn.ReLU()

        self.do1 = nn.Dropout(dropout_prob)
        self.do2 = nn.Dropout(dropout_prob)
        self.apply(init_weights)

    def forward(self, x):

        xx = x[1]
        out_sarc = self.fc12( self.r1 ( self.do1( self.fc11 (xx))))
        out_sent = self.fc22( self.r2 ( self.do2( self.fc21 (xx))))
        return [out_sarc,out_sent]

In [ ]:
def train(base_model, mt_classifier, iterator, optimizer, sarc_criterion, sent_criterion, scheduler):

    # set the model in eval phase
    base_model.train(True)
    mt_classifier.train(True)

    acc_sarcasm= 0
    acc_sentiment= 0

    f1_sarcasm =0
    f1_score_macro = 0

    loss= 0

    all_sarcasm_outputs = np.array([])
    all_sarcasm_labels = np.array([])

    all_sentiment_outputs = np.array([])
    all_sentiment_labels = np.array([])

    for data_input, sarc_label_input, sent_label_input  in Bar(iterator):

        for k, v in data_input.items():
            data_input[k] = v.to(device)

        for k, v in sarc_label_input.items():
            sarc_label_input[k] = v.long().to(device)

        for k, v in sent_label_input.items():
            sent_label_input[k] = v.long().to(device)

        optimizer.zero_grad()


        #forward pass

        sarcasm_target = sarc_label_input['sarcasm']

        sentiment_target = sent_label_input['sentiment']

        # forward pass

        output = base_model(**data_input)

        sarcasm_logits , sentiment_logits = mt_classifier(output)

        sarcasm_probs = torch.softmax(sarcasm_logits, dim=1)

        sentiment_probs = torch.softmax(sentiment_logits, dim=1)

        # print(sarcasm_logits )
        # print(sarcasm_target)

        # print(sentiment_logits )
        # print(sentiment_target)
        # print(sentiment_probs)
        # print(torch.max(sentiment_probs, 1))

        loss_sarcasm = sarc_criterion(sarcasm_logits, sarcasm_target)
        loss_sentiment = sent_criterion(sentiment_logits, sentiment_target)

        loss_ = loss_sarcasm + loss_sentiment
        # loss += loss_sarcasm.item()
        # loss += loss_sentiment.item()
        # backpropage the loss and compute the gradients
        loss_.backward()
        # loss_sarcasm.backward()
        # loss_sentiment.backward()

        optimizer.step()
        scheduler.step()

        acc_sarcasm += calc_accuracy(sarcasm_probs, sarcasm_target)
        _, predicted_sarcasm = torch.max(sarcasm_probs, 1)
        all_sarcasm_outputs = np.append(all_sarcasm_outputs, predicted_sarcasm.squeeze().cpu().numpy())
        all_sarcasm_labels = np.append(all_sarcasm_labels, sarcasm_target.squeeze().cpu().numpy())

        acc_sentiment += calc_accuracy(sentiment_probs, sentiment_target)
        _, predicted_sentiment = torch.max(sentiment_probs, 1)
        all_sentiment_outputs = np.append(all_sentiment_outputs, predicted_sentiment.squeeze().cpu().numpy())
        all_sentiment_labels = np.append(all_sentiment_labels, sentiment_target.squeeze().cpu().numpy())


    all_sarcasm_outputs = all_sarcasm_outputs.reshape(-1)
    all_sarcasm_labels = all_sarcasm_labels.reshape(-1)

    fscore_macro_sarc = f1_score(y_true=all_sarcasm_labels, y_pred=all_sarcasm_outputs, average='macro')
    fscore_sarcasm = f1_score(all_sarcasm_labels, all_sarcasm_outputs, average='binary', pos_label=1)

    all_sentiment_outputs = all_sentiment_outputs.reshape(-1)
    all_sentiment_labels = all_sentiment_labels.reshape(-1)

    fscore_macro_sent = f1_score(y_true=all_sentiment_labels, y_pred=all_sentiment_outputs, average='macro')


    accuracies = { 'acc_sarc': acc_sarcasm / len(iterator), 'f1_sarcastic': fscore_sarcasm, "f1_score_sarc": fscore_macro_sarc,
                   'acc_sent': acc_sentiment / len(iterator), "f1_score_sent": fscore_macro_sent}
    losses = { 'loss': loss_ / len(iterator)}

    return accuracies, losses


In [ ]:
extra = '_alpha'

In [ ]:
def train_full( config, train_loader, valid_loader):
    lr_o = config['lr_mult'] * config['lr']
    lr = config['lr']
    criterion = config['loss']
    #Instanciate models
    base_model = TransformerLayer(pretrained_path=config['pretrained_path'], both=True).to(device)
    mtl_classifier = ATTClassifier(base_model.output_num(), class_num_sarc=2, class_num_sent=3).to(device)
    # mtl_classifier = ClassifierMulti(base_model.output_num(), class_num=2, class_num2=3).to(device)


    # cls = 'ATTClassifier'

    # sarc_criterion = nn.CrossEntropyLoss().to(device)
    # sent_criterion = nn.CrossEntropyLoss().to(device)
    sarc_criterion = FocalLoss_Ori(num_class=2, alpha=[0.6, 2.89], gamma=2).to(device)
    sent_criterion = FocalLoss_Ori(num_class=3, alpha=[0.9,0.72,1.9], gamma=2).to(device)
    #

    params = [{'params':base_model.parameters(), 'lr':config['lr']}, {'params': mtl_classifier.parameters(), 'lr': config['lr']}]#, {'params':multi_task_loss.parameters(), 'lr': 0.0005}]
    optimizer = AdamW(params, lr=config["lr"])

    train_data_size = len(train_loader)
    steps_per_epoch = int(train_data_size / config['batch_size'])
    num_train_steps = len(train_loader) * config['epochs']
    warmup_steps = int(config['epochs'] * train_data_size * 0.1 / config['batch_size'])

    scheduler = get_linear_schedule_with_warmup(optimizer,  num_warmup_steps=warmup_steps, num_training_steps=num_train_steps)
    # Train model

    best_val_accuracy = 0
    best_val_f1_score_sarc = 0
    best_val_f1_sarcastic = 0

    best_val_accuracy_sent = 0
    best_val_f1_score_sent = 0

    best_val_metric = 0

    best_val_loss = float('+inf')

    best_report_sarcasm = None

    epo = 0

    for epoch in range(config['epochs']):
        # print("epoch {}".format(epoch + 1))

        train_accuracies, train_losses = train(base_model, mtl_classifier, train_loader, optimizer, sarc_criterion,sent_criterion,scheduler)
        valid_accuracies, valid_losses = evaluate(base_model, mtl_classifier, valid_loader, sarc_criterion,sent_criterion)

        val_loss = valid_losses['loss']
        total_val_metric = valid_accuracies['f1_score_sarc']
        print(valid_accuracies)

        if epoch == (config['epochs'] - 1):
        # if(total_val_metric >= best_val_f1_score_sarc):
            print('total_val_metric', total_val_metric)

            epo = epoch+1
            best_val_loss = val_loss
            best_val_metric = total_val_metric

            best_val_f1_score_sarc = valid_accuracies['f1_score_sarc']
            best_val_f1_sarcastic = valid_accuracies['f1_sarcastic']

            best_val_f1_score_sent = valid_accuracies['f1_score_sent']


            # best_report_sarcasm = valid_accuracies['report_sarcasm']
            best_val_accuracy_sarc = valid_accuracies['acc_sarc']
            best_val_accuracy_sent = valid_accuracies['acc_sent']

            best_val_loss = valid_losses['loss']

            print("save model's checkpoint")
            torch.save(base_model.state_dict(), f"./ckpts/best_basemodel_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth")
            torch.save(mtl_classifier.state_dict(), f"./ckpts/best_cls_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth")

    return best_val_accuracy_sarc, best_val_f1_score_sarc, best_val_f1_sarcastic, best_val_loss, epo, best_val_accuracy_sent, best_val_f1_score_sent

In [ ]:
def eval_full(config, loader1):
    criterion = config['loss']
    base_model = TransformerLayer(pretrained_path=config['pretrained_path'], both=True).to(device)
    classifier = ATTClassifier(base_model.output_num(), class_num_sarc=2, class_num_sent=3).to(device)
    # classifier = ClassifierMulti(base_model.output_num(), class_num=2, class_num2=3).to(device)
    base_model.load_state_dict(torch.load(f"./ckpts/best_basemodel_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth"))
    classifier.load_state_dict(torch.load(f"./ckpts/best_cls_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth"))
    base_model = base_model.to(device)
    classifier = classifier.to(device)
    df = pd.DataFrame()
    accuracies, all_outputs_pred, all_outputs_label, all_outputs_pred_sent, all_outputs_label_sent = predict(base_model, classifier, loader1)
    return accuracies, all_outputs_pred, all_outputs_label, all_outputs_pred_sent, all_outputs_label_sent

In [ ]:
def truncate(f, n):
    return math.floor(f * 10 ** n) / 10 ** n

In [ ]:
data_arr = ["ArSarcasm_v2"]
lr_arr = [4e-5,5e-5,6e-5]
batch_arr = [32]
epoch_arr = [1,2]
loss_arr=['FL']
seed_arr=[16826]

In [ ]:
for lr_i in lr_arr:
  for batch_i in batch_arr:
    for epoch_i in epoch_arr:
      for loss_i in loss_arr:
        for seed_i in seed_arr:
          data_i = data_arr[0]
          # seed_i= seed_arr[0]
          # lr_i = lr_arr[0]
          # batch_i= batch_arr[0]
          # loss_i = loss_arr[0]
          # epoch_i = epoch_arr[0]
          args = {}
          args['lr_mult'] = 1.0
          args['seed'] = seed_i
          args['num_worker'] = 4
          args['lang'] = 'ar'
          args['phase'] = 'train'
          args['lm_pretrained'] = 'marbert'

          args['lr'] =lr_i
          args['epochs'] = epoch_i
          args['batch_size'] = batch_i
          args['loss'] = loss_i
          config = {}
          config["max_length"] = 64
          config['args'] = args
          config["output_for_test"] = True
          config['epochs'] = args['epochs']
          config["class_num"] = 1
          config["lr"] = args['lr']
          config['lr_mult'] = args['lr_mult']
          config['batch_size'] = args['batch_size']
          config['lm'] = args['lm_pretrained']
          config['loss'] = args['loss']
          lang = args['lang']
          dosegmentation = False

          if args['lm_pretrained'] == 'marbert':
              config['pretrained_path'] = "UBC-NLP/MARBERT"


          RANDOM_SEED = config['args']['seed']

          random.seed(RANDOM_SEED)
          np.random.seed(RANDOM_SEED)
          torch.manual_seed(RANDOM_SEED)
          torch.cuda.manual_seed(RANDOM_SEED)
          torch.cuda.manual_seed_all(RANDOM_SEED)
          torch.backends.cudnn.deterministic = True
          torch.backends.cudnn.benchmark = False


          model_name = f"{config['args']['batch_size']}_{config['args']['loss']}_{config['args']['lr']}_{config['args']['epochs']}_{config['args']['seed']}{extra}"
          print('model_name', model_name)
          train_loader, valid_loader = loadTrainValData2(data_i, size = 0.2 ,batchsize=args['batch_size'], num_worker=0, pretraine_path=config['pretrained_path'], max_length=config['max_length'])

          best_val_accuracy_sarc, best_val_f1_score_sarc, best_val_f1_sarcastic, best_val_loss, best_epo, best_val_accuracy_sent, best_val_f1_score_sent  =train_full(config, train_loader, valid_loader)
          best_val_accuracy_sarc, best_val_f1_score_sarc, best_val_f1_sarcastic, best_val_loss, best_epo, best_val_accuracy_sent, best_val_f1_score_sent

          results = {'model_name' : f'{model_name}'}
          results['loss_fn']= config['args']['loss']
          results['batch_size']=config['args']['batch_size']
          results['lr']=config['args']['lr']
          results['f1_sarcastic'] = best_val_f1_sarcastic
          results['f1_score_sarc'] = best_val_f1_score_sarc
          results['f1_score_sent'] = best_val_f1_score_sent
          results['epoch']=config['args']['epochs']
          results['seed']=config['args']['seed']
          results2 = {'model_name' : f'{model_name}'}
          results2['loss_fn']= config['args']['loss']
          results2['batch_size']=config['args']['batch_size']
          results2['lr']=config['args']['lr']
          results2['f1_sarcastic'] = truncate(best_val_f1_sarcastic,2)
          results2['f1_score_sarc'] = truncate(best_val_f1_score_sarc,2)
          results2['f1_score_sent'] = truncate(best_val_f1_score_sent,2)
          results2['epoch']=config['args']['epochs']
          results2['seed']=config['args']['seed']
          with open(results_h, 'a+') as f:
                f.write(json.dumps(results) + '\n')
          with open(results_h_2, 'a+') as f:
                f.write(json.dumps(results2) + '\n')
          results_db_h = pd.read_json(results_h, lines=True)
          print("results_db_h", results_db_h)
          args['phase'] = 'predict'
          config['args'] = args
          test_loader = loadTestData(data_i,batchsize=args['batch_size'], num_worker=0, pretraine_path=config['pretrained_path'],  max_length=config['max_length'])


          test_accuracies, test_all_outputs_sarc, test_all_labels_sarc, test_all_outputs_sent, test_all_labels_sent = eval_full(config, loader1=test_loader)

          results = {'model_name' : f'{model_name}'}
          results['loss_fn']= config['args']['loss']
          results['batch_size']=config['args']['batch_size']
          results['lr']=config['args']['lr']
          results['f1_sarcastic'] = test_accuracies['f1_sarcastic']
          results['f1_score_sarc'] = test_accuracies['f1_score_sarc']
          results['f1_score_sent'] = test_accuracies['f1_score_sent']
          results['epoch']=config['args']['epochs']
          results['seed']=config['args']['seed']
          results2 = {'model_name' : f'{model_name}'}
          results2['loss_fn']= config['args']['loss']
          results2['batch_size']=config['args']['batch_size']
          results2['lr']=config['args']['lr']
          results2['f1_sarcastic'] = truncate(test_accuracies['f1_sarcastic'],2)
          results2['f1_score_sarc'] = truncate(test_accuracies['f1_score_sarc'],2)
          results2['f1_score_sent'] = truncate(test_accuracies['f1_score_sent'],2)
          results2['epoch']=config['args']['epochs']
          results2['seed']=config['args']['seed']
          with open(results_t, 'a+') as f:
                f.write(json.dumps(results) + '\n')
          with open(results_t_2, 'a+') as f:
                f.write(json.dumps(results2) + '\n')
          results_db_t = pd.read_json(results_t, lines=True)
          print("results_db_t", results_db_t)

          shutil.copy(f"./ckpts/best_basemodel_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth", f"drive/MyDrive/iSarcasm/{folder_path}/bert/models/best_basemodel_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth")
          shutil.copy(f"./ckpts/best_cls_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth", f"drive/MyDrive/iSarcasm/{folder_path}/bert/models/best_cls_sarcasm_{config['batch_size']}_{config['loss']}_{config['lr']}_ml{config['max_length']}_{config['epochs']}_{config['args']['seed']}_sarcat{extra}.pth")

model_name 32_FL_4e-05_1_16826_alpha


Streaming output truncated to the last 5000 lines.
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-19-48bcdcf4f651>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-19-48bcdcf4f651>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-19-48bcdcf4f651>:21:

tokenizer_config.json:   0%|          | 0.00/376 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/701 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/1.10M [00:00<?, ?B/s]

...

3000/3000: [===============================>] - ETA 0.2s
results_db_t                    model_name loss_fn  batch_size       lr  f1_sarcastic  \
0   16_FL_1e-05_1_16826_alpha      FL          16  0.00001      0.613043   
1   16_FL_1e-05_2_16826_alpha      FL          16  0.00001      0.626506   
2   16_FL_1e-05_3_16826_alpha      FL          16  0.00001      0.627076   
3   16_FL_2e-05_1_16826_alpha      FL          16  0.00002      0.619068   
4   16_FL_2e-05_2_16826_alpha      FL          16  0.00002      0.629829   
5   16_FL_2e-05_3_16826_alpha      FL          16  0.00002      0.621964   
6   16_FL_3e-05_1_16826_alpha      FL          16  0.00003      0.612489   
7   16_FL_3e-05_2_16826_alpha      FL          16  0.00003      0.623853   
8   16_FL_3e-05_3_16826_alpha      FL          16  0.00003      0.616372   
9   16_FL_4e-05_1_16826_alpha      FL          16  0.00004      0.619561   
10  16_FL_4e-05_2_16826_alpha      FL          16  0.00004      0.623145   
11  16_FL_4e-05_3_

Streaming output truncated to the last 5000 lines.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-19-48bcdcf4f651>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-19-48bcdcf4f651>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-19-48bcdcf4f651>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of

10038/10038: [===============================>] - ETA 0.4s
2510/2510: [===============================>] - ETA 0.1s
{'acc_sarc': 0.7689873417721519, 'f1_sarcastic': 0.576271186440678, 'f1_score_sarc': 0.7096480147327605, 'acc_sent': 0.7371722423146474, 'f1_score_sent': 0.7242819364187746}
10038/10038: [===============================>] - ETA 0.4s
2510/2510: [===============================>] - ETA 0.1s
{'acc_sarc': 0.8308092224231465, 'f1_sarcastic': 0.6195652173913044, 'f1_score_sarc': 0.756156459563885, 'acc_sent': 0.7697219710669078, 'f1_score_sent': 0.7577100429540861}
total_val_metric 0.756156459563885
save model's checkpoint
results_db_h                    model_name loss_fn  batch_size       lr  f1_sarcastic  \
0   16_FL_1e-05_1_16826_alpha      FL          16  0.00001      0.596835   
1   16_FL_1e-05_2_16826_alpha      FL          16  0.00001      0.622723   
2   16_FL_1e-05_3_16826_alpha      FL          16  0.00001      0.621818   
3   16_FL_2e-05_1_16826_alpha      FL       

Streaming output truncated to the last 5000 lines.
<ipython-input-20-59698643f9aa>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-20-59698643f9aa>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels[data['sentiment'][i]]
<ipython-input-20-59698643f9aa>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['sentiment'][i] = dic_labels

3000/3000: [===============================>] - ETA 0.2s
results_db_t                    model_name loss_fn  batch_size       lr  f1_sarcastic  \
0   16_FL_1e-05_1_16826_alpha      FL          16  0.00001      0.613043   
1   16_FL_1e-05_2_16826_alpha      FL          16  0.00001      0.626506   
2   16_FL_1e-05_3_16826_alpha      FL          16  0.00001      0.627076   
3   16_FL_2e-05_1_16826_alpha      FL          16  0.00002      0.619068   
4   16_FL_2e-05_2_16826_alpha      FL          16  0.00002      0.629829   
5   16_FL_2e-05_3_16826_alpha      FL          16  0.00002      0.621964   
6   16_FL_3e-05_1_16826_alpha      FL          16  0.00003      0.612489   
7   16_FL_3e-05_2_16826_alpha      FL          16  0.00003      0.623853   
8   16_FL_3e-05_3_16826_alpha      FL          16  0.00003      0.616372   
9   16_FL_4e-05_1_16826_alpha      FL          16  0.00004      0.619561   
10  16_FL_4e-05_2_16826_alpha      FL          16  0.00004      0.623145   
11  16_FL_4e-05_3_

In [ ]:
results_db_h = pd.read_json(results_h, lines=True)
print("results_db_h", results_db_h)

results_db_h                    model_name loss_fn  batch_size       lr  f1_sarcastic  \
0   16_FL_1e-05_1_16826_alpha      FL          16  0.00001      0.596835   
1   16_FL_1e-05_2_16826_alpha      FL          16  0.00001      0.622723   
2   16_FL_1e-05_3_16826_alpha      FL          16  0.00001      0.621818   
3   16_FL_2e-05_1_16826_alpha      FL          16  0.00002      0.597523   
4   16_FL_2e-05_2_16826_alpha      FL          16  0.00002      0.611702   
5   16_FL_2e-05_3_16826_alpha      FL          16  0.00002      0.618677   
6   16_FL_3e-05_1_16826_alpha      FL          16  0.00003      0.603476   
7   16_FL_3e-05_2_16826_alpha      FL          16  0.00003      0.610659   
8   16_FL_3e-05_3_16826_alpha      FL          16  0.00003      0.613746   
9   16_FL_4e-05_1_16826_alpha      FL          16  0.00004      0.602201   
10  16_FL_4e-05_2_16826_alpha      FL          16  0.00004      0.608295   
11  16_FL_4e-05_3_16826_alpha      FL          16  0.00004      0.628180   

In [ ]:
results_db_t = pd.read_json(results_t, lines=True)
print("results_db_t", results_db_t)

results_db_t                    model_name loss_fn  batch_size       lr  f1_sarcastic  \
0   16_FL_1e-05_1_16826_alpha      FL          16  0.00001      0.613043   
1   16_FL_1e-05_2_16826_alpha      FL          16  0.00001      0.626506   
2   16_FL_1e-05_3_16826_alpha      FL          16  0.00001      0.627076   
3   16_FL_2e-05_1_16826_alpha      FL          16  0.00002      0.619068   
4   16_FL_2e-05_2_16826_alpha      FL          16  0.00002      0.629829   
5   16_FL_2e-05_3_16826_alpha      FL          16  0.00002      0.621964   
6   16_FL_3e-05_1_16826_alpha      FL          16  0.00003      0.612489   
7   16_FL_3e-05_2_16826_alpha      FL          16  0.00003      0.623853   
8   16_FL_3e-05_3_16826_alpha      FL          16  0.00003      0.616372   
9   16_FL_4e-05_1_16826_alpha      FL          16  0.00004      0.619561   
10  16_FL_4e-05_2_16826_alpha      FL          16  0.00004      0.623145   
11  16_FL_4e-05_3_16826_alpha      FL          16  0.00004      0.619125   